In [1]:
import pandas as pd

from sodapy import Socrata

from timeit import default_timer

import json



# Unauthenticated client only works with public data sets. Note 'None'

# in place of application token, and no username or password:

client = Socrata("data.cityofnewyork.us", None)



# Example authenticated client (needed for non-public datasets):

# client = Socrata(data.cityofnewyork.us,

#                  MyAppToken,

#                  userame="user@example.com",

#                  password="AFakePassword")



# First 2000 results, returned as JSON from API / converted to Python list of

# dictionaries by sodapy.home/steven/Documents/DataMining/Velo_Archive/velostation.csv

start = default_timer()



# do stuff

#16385532

results = client.get("pqfs-mqru",limit=10000)

# Convert to pandas DataFrame

results_df = pd.DataFrame.from_records(results)

with open('taxisTenThousands.json', 'w') as outfile:
    json.dump(results, outfile)

duration = default_timer() - start

print(duration/60)

0.03402464275000057


In [11]:
from datetime import datetime

string = "2016-01-01T00:19:33.000"

datetime_arr = []

if 'T' in string: 
    datetime_arr = string.split('T')
    date = datetime_arr[0]
    time = datetime_arr[1]

date = datetime.strptime(string[:-4], '%Y-%m-%dT%H:%M:%S')

print(str(date))

2016-01-01 00:19:33


In [2]:
import json
import os
import csv

from timeit import default_timer

start = default_timer()

infile = open("taxisTenThousands.json", "r")

outfile = open("Taxis_Ten_Thousands.csv", "w")

writer = csv.writer(outfile)


#header_writer = csv.DictWriter(outfile, fieldnames = ["dropoff_latitude", "dropoff_longitude", "extra", "fare_amount",

#                 "improvement_surcharge", "mta_tax", "passenger_count", "payment_type",

#                 "pickup_latitude", "pickup_longitude", "ratecodeid", "store_and_fwd_flag",

#                 "tip_amount", "tolls_amount", "total_amount", "lpep_dropoff_datetime",

#                 "lpep_pickup_datetime", "trip_distance", "vendorid"], delimiter = ',')
    

#header_writer.writeheader()
    


#writer.writerow(["dropoff_latitude", "dropoff_longitude", "extra", "fare_amount",
#
#                 "improvement_surcharge", "mta_tax", "passenger_count", "payment_type",
#
#                 "pickup_latitude", "pickup_longitude", "ratecodeid", "store_and_fwd_flag",
#
#                 "tip_amount", "tolls_amount", "total_amount", "tpep_dropoff_datetime",
#
#                 "tpep_pickup_datetime", "trip_distance", "vendorid"])

for row in json.loads(infile.read()):

    writer.writerow([row["dropoff_latitude"], row["dropoff_longitude"], row["extra"], row["fare_amount"],

                     row["improvement_surcharge"], row["mta_tax"], row["passenger_count"], row["payment_type"],

                     row["pickup_latitude"], row["pickup_longitude"], row["ratecodeid"], row["store_and_fwd_flag"],

                     row["tip_amount"], row["tolls_amount"], row["total_amount"], row["lpep_dropoff_datetime"],

                     row["lpep_pickup_datetime"], row["trip_distance"], row["vendorid"]])

    

duration = default_timer() - start

print('done! ' + str(duration/60))

done! 0.0036085028333369944


In [3]:
import pyspark
from pyspark.sql import SQLContext
from pyspark.sql.types import *
from pyspark import SparkContext

sc=SparkContext()

In [13]:
from datetime import datetime

def add_fields(line, separator): 
    fields = []
    
    values = line.split(separator)
    
    #dropoff_latitude
    fields.append(float(values[0]))
    
    #dropoff_longitude
    fields.append(float(values[1]))
    
    #extra
    fields.append(float(values[2]))
    
    #fare_amount
    fields.append(float(values[3]))
    
    #improvement_surcharge
    fields.append(float(values[4]))
    
    #mta_tax
    fields.append(float(values[5]))
    
    #passenger_count
    fields.append(int(values[6]))
    
    #payment_type
    fields.append(int(values[7]))
    
    #pickup_latitude
    fields.append(float(values[8]))
    
    #pickup_longitude
    fields.append(float(values[9]))
    
    #ratecodeid
    fields.append(int(values[10]))
    
    #store_and_fwd_flag
    fields.append(str(values[11]))
    
    #tip_amount
    fields.append(float(values[12]))
    
    #tolls_amount
    fields.append(float(values[13]))
    
    #total_amount
    fields.append(float(values[14]))
    
    #lpep_dropoff_datetime
    fields.append(datetime.strptime(values[15][:-4], '%Y-%m-%dT%H:%M:%S'))
    
    #lpep_pickup_datetime
    fields.append(datetime.strptime(values[16][:-4], '%Y-%m-%dT%H:%M:%S'))
    
    #trip_distance
    fields.append(float(values[17]))
    
    #vendorid
    fields.append(int(values[18]))
    
    return fields
    

In [17]:
from timeit import default_timer

#"_id", "dropoff_latitude", "dropoff_longitude", "extra", "fare_amount", "improvement_surcharge", "lpep_dropoff_datetime"
#"lpep_pickup_datetime", "mta_tax", "passenger_count", "payment_type", "pickup_latitude", "pickup_longitude", "ratecodeid"
#"store_and_fwd_flag", tip_amount", "tolls_amount", "total_amount", "trip_distance", "trip_type", "vendorid"

def convert_to_df():
    separator = ','
    
    taxis_data = sc.textFile('Taxis_Ten_Thousands.csv')
    taxis_rdd = (taxis_data                    
                    .map(lambda l: add_fields(l, separator)))
    
    #header = taxis_rdd.first
    #taxis_rdd = taxis_rdd.filter(lambda l: l != header)
    
    taxis_df = sqlContext.createDataFrame(taxis_rdd, schema)
    
    return taxis_df

start = default_timer()


fields = []

fields.append(StructField('dropoff_latitude', FloatType(), True))
fields.append(StructField('dropoff_longitude', FloatType(), True))
fields.append(StructField('extra', FloatType(), True))
fields.append(StructField('fare_amount', FloatType(), True))
fields.append(StructField('improvement_surcharge', FloatType(), True))
fields.append(StructField('mta_tax', FloatType(), True))
fields.append(StructField('passenger_count', IntegerType(), True))
fields.append(StructField('payment_type', IntegerType(), True))
fields.append(StructField('pickup_latitude', FloatType(), True))
fields.append(StructField('pickup_longitude', FloatType(), True))
fields.append(StructField('ratecodeid', IntegerType(), True))
fields.append(StructField('store_and_fwd_flag', StringType(), True))
fields.append(StructField('tip_amount', FloatType(), True))
fields.append(StructField('tolls_amount', FloatType(), True))
fields.append(StructField('total_amount', FloatType(), True))
fields.append(StructField('lpep_dropoff_datetime', DateType(), True))
fields.append(StructField('lpep_pickup_datetime', DateType(), True))
fields.append(StructField('trip_distance', FloatType(), True))
fields.append(StructField('vendorid', IntegerType(), True))

schema = StructType(fields)
sqlContext=SQLContext(sc)

convert_to_df().registerTempTable("Taxis")
sql = "SELECT * FROM Taxis"

taxis_data = []
taxis_data.append(sqlContext.sql("SELECT * FROM Taxis").collect())

print(taxis_data)

duration = default_timer() - start

print('done! ' + str(duration/60))


[[Row(dropoff_latitude=40.69804382324219, dropoff_longitude=-73.92427825927734, extra=0.5, fare_amount=8.0, improvement_surcharge=0.30000001192092896, mta_tax=0.5, passenger_count=1, payment_type=1, pickup_latitude=40.68061065673828, pickup_longitude=-73.92864227294922, ratecodeid=1, store_and_fwd_flag='N', tip_amount=1.8600000143051147, tolls_amount=0.0, total_amount=11.15999984741211, lpep_dropoff_datetime=datetime.date(2016, 1, 1), lpep_pickup_datetime=datetime.date(2016, 1, 1), trip_distance=1.4600000381469727, vendorid=2), Row(dropoff_latitude=40.76137924194336, dropoff_longitude=-73.92391967773438, extra=0.5, fare_amount=15.5, improvement_surcharge=0.30000001192092896, mta_tax=0.5, passenger_count=1, payment_type=2, pickup_latitude=40.723175048828125, pickup_longitude=-73.95267486572266, ratecodeid=1, store_and_fwd_flag='N', tip_amount=0.0, tolls_amount=0.0, total_amount=16.799999237060547, lpep_dropoff_datetime=datetime.date(2016, 1, 1), lpep_pickup_datetime=datetime.date(2016, 